# 通过 API 使用托管 ComfyUI 工作流

ComfyUI 是一套生图领域常用的工作流（workflow）编排工具，可以方便灵活的设计图片处理工作流。无问芯穹 GenStudio 提供了 ComfyUI 工作流托管和 API 服务化平台，用户仅需托管工作流，在业务中对接 API 服务，由平台负责维护服务、增减算力和优化效率。

## 简介

本文描述了与 ComfyUI 通信的 API 端点的基本结构，并结合 Python 代码描述了详细的托管、数据前处理、和 API 对接流程。

您将了解：

- 如何在 GenStudio 中创建托管的 ComfyUI 工作流。
- 如何搭建一个文生图的 API 流程。
- 如何搭建一个图生图的 API 流程。
- 如何在业务流程中修改工作流参数。

## 托管 ComfyUI 工作流

### 导出 API Format 工作流

要通过 API 使用 ComfyUI 工作流，请使用"Save（API Format）"保存工作流。如果没有此按钮，必须通过单击右上角的设置按钮（齿轮图标）启用 "Enable Dev Mode options"。

### 上传  API Format 工作流

1. 登录到 [ComfyUI Workflow 管理](https://maas.cloud.infini-ai.com/genstudio/workflow) 页面。
2. 点击**上传 Workflow** 按钮，选择从 ComfyUI 导出的 API JSON 格式的工作流文件。
3. 上传文件，校验通过后，输入工作流名称。

通过上述步骤，我们已完成在 ComfyUI 中的处理。后续在搭建 API 流程时，我们将使用 GenStudio 平台，获取工作流 ID 和工作流参数。

## API 鉴权设置

使用 API 服务，首先需要完成身份验证。请按照以下步骤获取您的 API 密钥：

1. 登录到 [密钥管理](https://cloud.infini-ai.com/genstudio/secret/key) 页面。
2. 复制已有的 API 密钥，或自助创建 API Key。
3. 点击复制按钮获取密钥。您可能需要完成二次验证。


## Jupyter Notebook 设置

在 Jupyter Notebook 中，我们首先设置全局变量和导入必要的库。

In [ ]:
import os
import requests
import time
import json
import random
from PIL import Image
import io
from urllib.parse import urlparse

# 设置全局变量
# 设置 API 密钥和服务器地址
API_KEY = os.getenv('COMFYUI_API_KEY')
SERVER_ADDRESS = os.getenv('COMFYUI_SERVER_ADDRESS')
# 设置默认工作流 ID
DEFAULT_WORKFLOW_ID = os.getenv('DEFAULT_WORKFLOW_ID')
# 设置默认输出路径
DEFAULT_OUTPUT_PATH = os.getenv('DEFAULT_OUTPUT_PATH')
# 设置图生图默认上传路径
DEFAULT_INPUT_PATH = os.getenv('DEFAULT_INPUT_PATH')
# 设置 ComfyUI API JSON 文生图 Workflow 文件路径
COMFY_T2I_WORKFLOW_API_JSON_PATH = os.getenv('COMFY_T2I_WORKFLOW_API_JSON_PATH')
# 设置 ComfyUI API JSON 图生图 Workflow 文件路径
COMFY_I2I_WORKFLOW_API_JSON_PATH = os.getenv('COMFY_I2I_WORKFLOW_API_JSON_PATH')
# 设置 ComfyUI 使用的 Checkpoint 名称
CHECKPOINT_NAME = os.getenv('CHECKPOINT_NAME')

# 如果环境变量未设置，你可以手动赋值：
API_KEY = ""
SERVER_ADDRESS = "cloud.infini-ai.com"
DEFAULT_WORKFLOW_ID = ""
DEFAULT_OUTPUT_PATH = './output'
COMFY_T2I_WORKFLOW_API_JSON_PATH='./comfy_exported_t2i_workflow_api.json'
# COMFY_I2I_WORKFLOW_API_JSON_PATH='./comfy_exported_i2i_workflow_api.json'
# Checkpoint 取值请以 GenStudio 工作流【查看参数】的中可选值为准
CHECKPOINT_NAME = 'common/sd1.5/majicMIX realistic 麦橘写实_v7.safetensors'

# 验证所有环境变量是否设置
environment_variables = [API_KEY, SERVER_ADDRESS, DEFAULT_WORKFLOW_ID, DEFAULT_OUTPUT_PATH, COMFY_T2I_WORKFLOW_API_JSON_PATH, CHECKPOINT_NAME]
if not all(environment_variables):
    missing_variables = [var_name for var_name, var_value in zip(['API_KEY', 'SERVER_ADDRESS', 'DEFAULT_WORKFLOW_ID', 'DEFAULT_OUTPUT_PATH', 'COMFY_t2i_WORKFLOW_API_JSON_PATH', 'CHECKPOINT_NAME'], environment_variables) if not var_value]
    raise ValueError(f"以下环境变量未设置：{', '.join(missing_variables)}")

print("所有全局变量已设置。")

## API 端点

GenStudio 托管的 Comfy 工作流服务提供了一套封装原始 ComfyUI HTTP 端点的新端点。以下是原始 ComfyUI 端点与 GenStudio ComfyUI API 端点之间的映射关系：

| 原始 ComfyUI 端点 | 描述 | 我们的 API 端点 |
|-------------------|------|-----------------|
| POST /prompt | 将提示排入工作流队列，返回 prompt_id 或错误 | POST /api/maas/comfy_task_api/prompt |
| GET /history/{prompt_id} | 返回给定 prompt_id 的队列或输出 | POST /api/maas/comfy_task_api/get_task_info |
| GET /view | 给定文件名、子文件夹和类型（"input"、"output"、"temp"），返回一个图像 | POST /api/maas/comfy_task_api/get_result |
| POST /upload/image | 给定 image_data 和类型（"input"、"output"、"temp"），将图像上传到 ComfyUI | POST /api/maas/comfy_task_api/upload/image |

这些 API 端点提供了与 ComfyUI 交互所需的基本功能，包括提交提示、检索历史、查看图像和上传图像。

### 提交任务

使用 `POST /api/maas/comfy_task_api/prompt` 端点发送请求，将其放入工作流队列。参数 `workflow_id` 用来引用托管的 ComfyUI 工作流。参数 `prompt` 是当前请求的提示词，可用于修改托管工作流中的提示文本和配置参数。

In [28]:

import requests
import json

def queue_prompt(workflow_id=DEFAULT_WORKFLOW_ID, prompt=None):
    """
    将提示排队处理。

    参数：
        workflow_id (str): 工作流ID。必需参数，但默认使用环境变量中的值。
        prompt (dict, 可选): 要处理的提示。默认为None。

    返回：
        dict: API的JSON响应，如果发生错误则返回None。

    异常：
        ValueError: 如果workflow_id为None或空字符串。
    """
    if not workflow_id:
        raise ValueError("workflow_id 是必需的，不能为空")

    url = f"https://{SERVER_ADDRESS}/api/maas/comfy_task_api/prompt"
    headers = {
        'Content-Type': 'application/json',
        'Authorization': f'Bearer {API_KEY}'
    }
    payload = {
        "workflow_id": workflow_id,
        "prompt": prompt
    }

    try:
        response = requests.post(url, headers=headers, json=payload)
        response.raise_for_status()
        return response.json()
    except requests.exceptions.RequestException as e:
        print(f"queue_prompt 出错，未能将生图请求加入队列: {e}")
        return None



### 获取任务信息

使用 `POST /api/maas/comfy_task_api/get_task_info` 端点获取 ComfyUI 生图任务的排队状态和生图结果。

In [29]:
def get_task_info(prompt_ids, url_expire_period=3600):
    url = f"https://{SERVER_ADDRESS}/api/maas/comfy_task_api/get_task_info"
    headers = {
        'Content-Type': 'application/json',
        'Authorization': f'Bearer {API_KEY}'
    }
    payload = {
        "comfy_task_ids": prompt_ids,
        "url_expire_period": url_expire_period
    }
    response = requests.post(url, headers=headers, json=payload)
    response.raise_for_status()
    print(f"获取任务信息成功，返回结果: {response.json()}")
    return response.json()


### 上传图像

使用 `POST /api/maas/comfy_task_api/upload/image` 端点上传图像。在图生图的流程中，我们需要获取上传图像后返回的 OSS Key，将该 Key 填入 Load Image 节点。

In [30]:
import requests

def upload_image(file_path):
    """
    将提示排队处理。

    参数：
        filepath (str): 本地图片路径，支持 png/jpg/jpeg,webp。

    """
    url = f"https://{SERVER_ADDRESS}/api/maas/comfy_task_api/upload/image"
    headers = {
        'Authorization': f'Bearer {API_KEY}'
    }
    with open(file_path, 'rb') as file:
        files = {'source_file': (os.path.basename(file_path), file, 'image/png')}
        response = requests.post(url, headers=headers, files=files)
    response.raise_for_status()
    return response.json()['data']['image_id']
 # 打印上传结果，包含 image_id

## 搭建文生图 API 工作流

### 获取 Base Promt

调用 `POST /api/maas/comfy_task_api/prompt` 端点时，如果不修改托管工作流的任何参数，仅需传入 `workflow_id`。如需需要修改托管工作流参数，则必须传入 `Promt`。

我们需要访问 GenStudio 托管的工作流，通过**查看参数**按钮复制全部参数，经过特殊处理后生成 Base Promt，便于后续传值和修改参数。

> `prompt` 参数的输入值并非 ComfyUI 导出的 Workflow API JSON 文件。

复制 GenStudio 托管工作流中的全部参数，并使用以下代码生成 Base Promt。


In [31]:
def get_prompt_json_body(api_params):
    prompt_json_body = {}
    
    for key, value in api_params.items():
        # Initialize the new structure with top-level keys
        prompt_json_body[key] = {'inputs': {}}
        
        # Focus on 'inputs' only
        if 'inputs' in value:
            for input_key, input_value in value['inputs'].items():
                # Swap the value to 'current' in the sub-level objects
                prompt_json_body[key]['inputs'][input_key] = input_value.get('current')

    return prompt_json_body

# Example usage
api_params_by_genstudio = {
  "3": {
    "inputs": {
      "seed": {
        "type": "INT",
        "current": 1,
        "spec": {
          "default": 0,
          "min": 0,
          "max": 18446744073709552000
        }
      },
      "steps": {
        "type": "INT",
        "current": 20,
        "spec": {
          "default": 20,
          "min": 1,
          "max": 10000
        }
      },
      "cfg": {
        "type": "FLOAT",
        "current": 7,
        "spec": {
          "default": 8,
          "min": 0,
          "max": 100,
          "step": 0.1,
          "round": 0.01
        }
      },
      "sampler_name": {
        "type": "LIST",
        "current": "ddim",
        "spec": {
          "choices": [
            "euler",
            "euler_cfg_pp",
            "euler_ancestral",
            "euler_ancestral_cfg_pp",
            "heun",
            "heunpp2",
            "dpm_2",
            "dpm_2_ancestral",
            "lms",
            "dpm_fast",
            "dpm_adaptive",
            "dpmpp_2s_ancestral",
            "dpmpp_sde",
            "dpmpp_sde_gpu",
            "dpmpp_2m",
            "dpmpp_2m_alt",
            "dpmpp_2m_sde",
            "dpmpp_2m_sde_gpu",
            "dpmpp_3m_sde",
            "dpmpp_3m_sde_gpu",
            "ddpm",
            "lcm",
            "ipndm",
            "ipndm_v",
            "deis",
            "ddim",
            "uni_pc",
            "uni_pc_bh2"
          ]
        }
      },
      "scheduler": {
        "type": "LIST",
        "current": "karras",
        "spec": {
          "choices": [
            "normal",
            "karras",
            "exponential",
            "sgm_uniform",
            "simple",
            "ddim_uniform",
            "beta"
          ]
        }
      },
      "denoise": {
        "type": "FLOAT",
        "current": 1,
        "spec": {
          "default": 1,
          "min": 0,
          "max": 1,
          "step": 0.01
        }
      }
    },
    "class_type": "KSampler",
    "_meta": {
      "title": "KSampler"
    }
  },
  "4": {
    "inputs": {
      "ckpt_name": {
        "type": "MODEL",
        "current": "majicMIX realistic 麦橘写实_v7.safetensors",
        "spec": {
          "choices": [
            "SUPIR_pruned/SUPIR-v0F_fp16.safetensors",
            "SUPIR_pruned/SUPIR-v0Q_fp16.safetensors",
            "SVD/svd_xt.safetensors",
            "common/flux/flux1-dev-fp8.safetensors",
            "common/flux/flux1-schnell-fp8.safetensors",
            "common/sd1.5/AWPainting_v1.3.safetensors",
            "common/sd1.5/GhostMix鬼混_V2.0.safetensors",
            "common/sd1.5/juggernaut_reborn.safetensors",
            "common/sd1.5/majicMIX realistic 麦橘写实_v7.safetensors",
            "common/sd1.5/v1-5-pruned-emaonly.safetensors",
            "common/sd1.5/美女AnyCharacterMix (Baked Vae)_v2.0 baked vae.safetensors",
            "common/sd3/sd3_medium.safetensors",
            "common/sd3/sd3_medium_incl_clips.safetensors",
            "common/sd3/sd3_medium_incl_clips_t5xxlfp16.safetensors",
            "common/sd3/sd3_medium_incl_clips_t5xxlfp8.safetensors",
            "common/sdxl/ArtiWaifu Diffusion 1.0 vae_0.1.safetensors",
            "common/sdxl/LEOSAM AIArt 兔狲插画 SDXL大模型_v1.safetensors",
            "common/sdxl/LEOSAM HelloWorld 新世界 | SDXL大模型_v2.safetensors",
            "common/sdxl/SDXL-Anime | 天空之境 _v3.1.safetensors",
            "common/sdxl/SDXL_ArienMixXL_V4.5.safetensors",
            "common/sdxl/SHMILY绚丽多彩_V1.0.safetensors",
            "common/sdxl/promissingRealistic_v35.safetensors",
            "common/sdxl/sd_xl_base_1.0.safetensors",
            "common/sdxl/sd_xl_refiner_1.0.safetensors",
            "flux/lcm_lora_sd15.safetensors",
            "sd1.5/majicMIX realistic 麦橘写实_v7.safetensors",
          ]
        }
      }
    },
    "class_type": "CheckpointLoaderSimple",
    "_meta": {
      "title": "Load Checkpoint"
    }
  },
  "5": {
    "inputs": {
      "width": {
        "type": "INT",
        "current": 512,
        "spec": {
          "default": 512,
          "min": 16,
          "max": 16384,
          "step": 8
        }
      },
      "height": {
        "type": "INT",
        "current": 512,
        "spec": {
          "default": 512,
          "min": 16,
          "max": 16384,
          "step": 8
        }
      },
      "batch_size": {
        "type": "INT",
        "current": 1,
        "spec": {
          "default": 1,
          "min": 1,
          "max": 4096
        }
      }
    },
    "class_type": "EmptyLatentImage",
    "_meta": {
      "title": "Empty Latent Image"
    }
  },
  "6": {
    "inputs": {
      "text": {
        "type": "STRING",
        "current": "a girl",
        "spec": {}
      }
    },
    "class_type": "CLIPTextEncode",
    "_meta": {
      "title": "CLIP Text Encode (Prompt)"
    }
  },
  "7": {
    "inputs": {
      "text": {
        "type": "STRING",
        "current": "",
        "spec": {}
      }
    },
    "class_type": "CLIPTextEncode",
    "_meta": {
      "title": "CLIP Text Encode (Prompt)"
    }
  }
}

prompt_from_api_params = get_prompt_json_body(api_params_by_genstudio)

### 制作节点 ID 映射表

为了方便后续定位待修改节点，需要再次用到 ComfyUI 导出的 Workflow API JSON 文件，我们将从中获取节点 ID 与 Class type 的映射表。这个函数将在修改工作流参数时用于查询节点 ID。


In [32]:
# import json
def get_id_to_class_type_map(comfy_workflow_api_json_path):
    try:
        with open(comfy_workflow_api_json_path, 'r', encoding='utf-8') as f:
            data = json.load(f)
    except FileNotFoundError:
        print(f"未找到文件 {comfy_workflow_api_json_path}")
        return None
    except json.JSONDecodeError:
        print(f"文件 {comfy_workflow_api_json_path} 包含无效的 JSON。")
        return None

    id_to_class_type = {}

    for node_id, node_data in data.items():
        # Default mapping
        id_to_class_type[node_id] = node_data['class_type']

    # Special handling for KSampler node
    for node_id, node_data in data.items():
        if node_data['class_type'] == 'KSampler':
            positive_input_id = node_data['inputs'].get('positive', [None])[0]
            negative_input_id = node_data['inputs'].get('negative', [None])[0]

            if positive_input_id is not None:
                id_to_class_type[positive_input_id] = 'positive_input_id'
            if negative_input_id is not None:
                id_to_class_type[negative_input_id] = 'negative_input_id'

    # Return the dictionary
    return id_to_class_type

### 获取和保存图像

定义两个工具函数，用于获取和保存生成的图像。这些函数将在下一步的 `generate_image_by_prompt` 函数中使用。

In [33]:
# import os
# import image
# from urllib.parse import urlparse


def get_images(files_dict):
    """
    从给定的文件字典中获取图像。

    参数:
        files_dict (dict): 包含图像URL的字典。键是图像类型标识符，值是URL列表。

    返回:
        list: 包含图像信息的字典列表。每个字典包含以下键：
            - 'file_name': 图像文件名
            - 'image_data': 图像二进制数据
            - 'type': 图像类型 ('output')
            - 'key': 原字典中的键

    异常:
        打印获取图像失败的错误信息，但不中断程序执行。
    """
    output_images = []
    for key, urls in files_dict.items():
        for url in urls:
            try:
                response = requests.get(url)
                response.raise_for_status()
                file_name = os.path.basename(urlparse(url).path.split('?')[0])  # Remove query parameters from filename
                output_images.append({
                    'file_name': file_name,
                    'image_data': response.content,
                    'type': 'output',
                    'key': key
                })
            except Exception as e:
                print(f"获取图像失败 {url}: {e}")
    return output_images

def save_images(images, output_path, save_previews):
    """
    将图像保存到指定路径。

    参数:
        images (list): 包含图像信息的字典列表。每个字典应包含以下键：
            - 'file_name': 图像文件名
            - 'image_data': 图像二进制数据
            - 'type': 图像类型 ('output' 或 'temp')
            - 'key': 用于创建子目录的键
        output_path (str): 保存图像的基本路径，以出图节点 ID 为子目录名称
        save_previews (bool): 是否保存预览图像（类型为'temp'的图像）

    返回:
        None

    异常:
        打印保存图像失败的错误信息，但不中断程序执行。
    """
    for item in images:
        directory = os.path.join(output_path, item['key'])
        if item['type'] == 'temp' and save_previews:
            directory = os.path.join(directory, 'temp')
        os.makedirs(directory, exist_ok=True)
        try:
            if 'image_data' not in item or item['image_data'] is None:
                print(f"跳过保存图像 {item.get('file_name', 'unknown')}: 没有图像数据")
                continue
            image = Image.open(io.BytesIO(item['image_data']))
            image.save(os.path.join(directory, item['file_name']))
            print(f"成功保存图像: {os.path.join(directory, item['file_name'])}")
        except Exception as e:
            print(f"保存图像 {item.get('file_name', 'unknown')} 失败: {e}")

### 处理与 API 的交互

`generate_image_by_prompt` 函数负责实际处理与 GenStudio ComfyUI API 的交互，包括提交请求、等待任务完成、检索结果和保存图像。以下是该函数的实现：

In [34]:
# import json
# import time

def generate_image_by_prompt(workflow_id=DEFAULT_WORKFLOW_ID, prompt=None, output_path=DEFAULT_OUTPUT_PATH, save_previews=False):
    """
    根据提示生成图像并保存到指定路径。

    参数：
        workflow_id (str): 工作流ID。默认使用环境变量中的值。
        prompt (dict, 可选): 用于生成图像的提示。默认为None。
        output_path (str): 保存生成图像的路径。此参数是必需的。
        save_previews (bool): 是否保存预览图像。默认为False。

    返回：
        dict: 包含prompt_id和生成的图像数据的字典。失败时返回None。

    异常：
        ValueError: 如果workflow_id为None或空字符串，或者output_path为None或空字符串。
    """
    if not workflow_id:
        raise ValueError("workflow_id 是必需的，不能为空")
    if not output_path:
        raise ValueError("output_path 是必需的，不能为空")

    try:
        print(f"提交图像请求，使用 Prompt: {prompt}")
        response = queue_prompt(workflow_id, prompt)
        prompt_id = response['data']['prompt_id']
        
        while True:
            task_info = get_task_info([prompt_id])
            if task_info['code'] != 0:
                raise Exception(f"获取任务信息失败: {task_info['msg']}")
            
            comfy_task_info = task_info['data']['comfy_task_info'][0]
            status = comfy_task_info['status']
            if status == 3:  # 已完成
                break
            elif status == 4:  # 失败
                raise Exception(f"任务失败: {comfy_task_info['errMsg']}")
            time.sleep(5)  # 等待 5 秒后再次检查
        
        files_dict = comfy_task_info.get('files', {})
        images = get_images(files_dict)
        save_images(images, output_path, save_previews)
        
        return prompt_id
    except Exception as e:
        print(f"生成图像时发生错误: {e}")
        return None
    

### 修改工作流参数

为了重复使用托管的特定工作流（`workflow_id`），同时能够更改正面提示，负面提示，seed，cfg 等参数以生成不同的图像，我们需要在 Base Prompt 中找到相关节点并调整参数值。

此时我们使用前面制作的节点 ID 映射表（`id_to_class_type`），在给定的的 Base Promt 中寻找节点、修改参数。

In [35]:
# import json
# import random

def prompt_to_image(workflow_id=DEFAULT_WORKFLOW_ID, prompt=None, positive_prompt=None, negative_prompt='', output_path=None, save_previews=False):
    """
    根据给定的提示修改工作流并生成图像。

    参数：
        workflow_id (str): 工作流ID。默认使用环境变量中的值。
        prompt (dict 或 str): 工作流提示。如果为None，则直接使用原始工作流。
        positive_prompt (str, 可选): 正面提示文本。
        negative_prompt (str): 负面提示文本。默认为空字符串。
        output_path (str): 保存生成图像的路径。
        save_previews (bool): 是否保存预览图像。默认为False。

    返回：
        tuple: (修改后的工作流JSON字符串, prompt_id)。如果出错，则返回 (None, None)。

    异常：
        ValueError: 如果workflow_id为None或空字符串，或者output_path为None或空字符串。
    """
    if not workflow_id:
        raise ValueError("workflow_id是必需的，不能为空")
    if not output_path:
        raise ValueError("output_path是必需的，不能为空")

    try:
        if prompt is None:
            print("工作流的 Base Prompt 为空，直接调用生成函数")
            prompt_id = generate_image_by_prompt(workflow_id, None, output_path, save_previews)
            return None, prompt_id
        else:

            prompt = json.loads(prompt) if isinstance(prompt, str) else prompt
            print("加载工作流 Base Prompt: ", prompt)

            # 使用从节点 ID 到类型的映射 id_to_class_type，找到 CheckpointLoaderSimple 节点数字
            ckpt_name = next((key for key, value in id_to_class_type.items() if value == 'CheckpointLoaderSimple'), None)
            if ckpt_name is None:
                print("找不到 ckpt_name 节点")
                return None

            # 设置正确的 checkpoint 名称，必须以 GenStudio 返回的 checkpoint 名称为准
            prompt[ckpt_name]['inputs']['ckpt_name'] = CHECKPOINT_NAME


            # 使用从节点 ID 到类型的映射 id_to_class_type，找到 KSampler 节点数字
            k_sampler = next((key for key, value in id_to_class_type.items() if value == 'KSampler'), None)
            if k_sampler is None:
                print("找不到 KSampler 节点")
                return None

            # 为 KSampler 节点设置一个随机种子
            prompt[k_sampler]['inputs']['seed'] = random.randint(10**14, 10**15 - 1)

            # 获取 positive_input_id 和 negative_input_id
            positive_input_id = next((key for key, value in id_to_class_type.items() if value == 'positive_input_id'), None)
            negative_input_id = next((key for key, value in id_to_class_type.items() if value == 'negative_input_id'), None)

            # 更新正面提示
            if positive_input_id is not None:
                prompt[positive_input_id]['inputs']['text'] = positive_prompt

            # 如果提供了负面提示，则更新负面提示
            if negative_prompt != '' and negative_input_id is not None:
                prompt[negative_input_id]['inputs']['text'] = negative_prompt

        prompt_id = generate_image_by_prompt(workflow_id, prompt, output_path, save_previews)
        return json.dumps(prompt), prompt_id

    except Exception as e:
        print(f"处理提示时发生错误: {e}")
        return None, None



### 使用 API 工作流

使用文本提示到图像的 API 工作流：

In [ ]:
# 前面已生成了 Base Prompt，此处直接获取即可
base_workflow_prompt = prompt_from_api_params

# 为了方便修改 Base Promt，从 ComfyUI 导出的 Workflow API JSON 中
# 获取 node id 到 class type 的映射
id_to_class_type=get_id_to_class_type_map(COMFY_T2I_WORKFLOW_API_JSON_PATH)

# 修改 Base Prompt 中的提示词
positive_prompt = "Spiderman in a red suit standing in middle of a crowded place, skyscrapers in the background, cinematic, neon colors, realistic look"
negative_prompt = "ugly, deformed"

# 调用函数生成图像
modified_prompt, prompt_id = prompt_to_image(
    prompt=base_workflow_prompt,
    positive_prompt=positive_prompt,
    negative_prompt=negative_prompt,
    output_path="./output",
    save_previews=True
)

if prompt_id:
    print(f"修改后的 Prompt: {modified_prompt}")
    print(f"生图成功 Prompt ID: {prompt_id}")
else:
    print("生图失败")

## 搭建图生图 API 工作流

首先，您必须在 ComfyUI 中构建基本的图像到图像工作流程，使用加载图像（Load Image）和 VEA 编码（VEA Encode）节点。

### 修改工作流参数

在图生图的流程中，在 Base Prompt 中找到相关节点并调整参数值的逻辑与文生图的逻辑相同。主要区别在于修改 LoadImage 节点的输入，将输入改为 "POST /api/maas/comfy_task_api/upload/image" 返回的 `image_id`。

此时我们使用前面制作的节点 ID 映射表（`id_to_class_type`），在给定的的 Base Promt 中寻找节点、修改参数。

In [ ]:

# import json
# import random

def prompt_image_to_image(workflow_id=DEFAULT_WORKFLOW_ID, prompt=None, positive_prompt=None, negative_prompt='', input_path=DEFAULT_INPUT_PATH,output_path=None, save_previews=False):
    """
    根据给定的提示修改工作流并生成图像。

    参数：
        workflow_id (str): 工作流ID。默认使用环境变量中的值。
        prompt (dict 或 str): 工作流提示。如果为None，则直接使用原始工作流。
        positive_prompt (str, 可选): 正面提示文本。
        negative_prompt (str): 负面提示文本。默认为空字符串。
        input_path (str): 图生图的输入图片的路径。此参数是必需的。
        output_path (str): 保存生成图像的路径。
        save_previews (bool): 是否保存预览图像。默认为False。

    返回：
        tuple: (修改后的工作流JSON字符串, prompt_id)。如果出错，则返回 (None, None)。

    异常：
        ValueError: 如果workflow_id为None或空字符串，或者output_path为None或空字符串。
    """
    if not workflow_id:
        raise ValueError("workflow_id是必需的，不能为空")
    if not output_path:
        raise ValueError("output_path是必需的，不能为空")

    try:
        if prompt is None:
            print("工作流的 Base Prompt 为空，直接调用生成函数")
            prompt_id = generate_image_by_prompt(workflow_id, None, output_path, save_previews)
            return None, prompt_id
        else:

            prompt = json.loads(prompt) if isinstance(prompt, str) else prompt
            print("加载工作流 Base Prompt: ", prompt)

            # 使用从节点 ID 到类型的映射 id_to_class_type
            # 找到 LoadImage 节点数字
            load_image = next((key for key, value in id_to_class_type.items() if value == 'LoadImage'), None)
            if load_image is None:
                print("找不到 LoadImage 节点")

            # 上传图片到 OSS
            try:
                oss_image_id = upload_image(input_path)
                print(f"文件上传成功，image_id: {oss_image_id}")
            except requests.RequestException as e:
                print(f"上传请求失败: {e}")
            except KeyError as e:
                print(f"响应中未找到预期的数据结构: {e}")
            except Exception as e:
                print(f"发生未预期的错误: {e}")
            
            prompt[load_image]['image'] = oss_image_id

            # 使用从节点 ID 到类型的映射 id_to_class_type，找到 CheckpointLoaderSimple 节点数字
            ckpt_name = next((key for key, value in id_to_class_type.items() if value == 'CheckpointLoaderSimple'), None)
            if ckpt_name is None:
                print("找不到 ckpt_name 节点")
                return None

            # 设置正确的 checkpoint 名称，必须以 GenStudio 返回的 checkpoint 名称为准
            prompt[ckpt_name]['inputs']['ckpt_name'] = CHECKPOINT_NAME


            # 找到 KSampler 节点数字
            k_sampler = next((key for key, value in id_to_class_type.items() if value == 'KSampler'), None)
            if k_sampler is None:
                print("找不到 KSampler 节点")
                return None

            # 为 KSampler 节点设置一个随机种子
            prompt[k_sampler]['inputs']['seed'] = random.randint(10**14, 10**15 - 1)

            # 获取 positive_input_id 和 negative_input_id
            positive_input_id = next((key for key, value in id_to_class_type.items() if value == 'positive_input_id'), None)
            negative_input_id = next((key for key, value in id_to_class_type.items() if value == 'negative_input_id'), None)

            # 更新正面提示
            if positive_input_id is not None:
                prompt[positive_input_id]['inputs']['text'] = positive_prompt

            # 如果提供了负面提示，则更新负面提示
            if negative_prompt != '' and negative_input_id is not None:
                prompt[negative_input_id]['inputs']['text'] = negative_prompt

        prompt_id = generate_image_by_prompt(workflow_id, prompt, output_path, save_previews)
        return json.dumps(prompt), prompt_id

    except Exception as e:
        print(f"处理提示时发生错误: {e}")
        return None, None


### 处理与 API 的交互

`generate_image_by_prompt_and_image` 函数负责实际处理与 GenStudio ComfyUI API 的交互，包括上传图片、提交请求、等待任务完成、检索结果和保存图像。以下是该函数的实现：

In [ ]:
# import json
# import time

def generate_image_by_prompt_and_image(workflow_id=DEFAULT_WORKFLOW_ID, prompt=None, output_path=DEFAULT_OUTPUT_PATH, save_previews=False):
    """
    根据提示和输入图像生成新图像并保存到指定路径。

    参数：
        workflow_id (str): 工作流ID。默认使用环境变量中的值。
        prompt (dict, 可选): 用于生成图像的提示。默认为None。
        output_path (str): 保存生成图像的路径。此参数是必需的。
        save_previews (bool): 是否保存预览图像。默认为False。

    返回：
        str: 生成的prompt_id。失败时返回None。

    异常：
        ValueError: 如果workflow_id为None或空字符串，或者output_path为None或空字符串。
    """
    if not workflow_id:
        raise ValueError("workflow_id 是必需的，不能为空")
    if not output_path:
        raise ValueError("output_path 是必需的，不能为空")

    try:
        print(f"提交图像请求，使用 Prompt: {prompt}")
        response = queue_prompt(workflow_id, prompt)
        prompt_id = response['data']['prompt_id']
        
        while True:
            task_info = get_task_info([prompt_id])
            if task_info['code'] != 0:
                raise Exception(f"获取任务信息失败: {task_info['msg']}")
            
            comfy_task_info = task_info['data']['comfy_task_info'][0]
            status = comfy_task_info['status']
            if status == 3:  # 已完成
                break
            elif status == 4:  # 失败
                raise Exception(f"任务失败: {comfy_task_info['errMsg']}")
            time.sleep(5)  # 等待 5 秒后再次检查
        
        files_dict = comfy_task_info.get('files', {})
        images = get_images(files_dict)
        save_images(images, output_path, save_previews)
        
        return prompt_id
    except Exception as e:
        print(f"生成图像时发生错误: {e}")
        return None

使用图像到图像的 API 工作流：

In [ ]:
# 前面已生成了 Base Prompt，此处直接获取即可
base_workflow_prompt = prompt_from_api_params

# 为了方便修改 Base Promt，从 ComfyUI 导出的 Workflow API JSON 中
# 获取 node id 到 class type 的映射
id_to_class_type=get_id_to_class_type_map(COMFY_I2I_WORKFLOW_API_JSON_PATH)

# 修改 Base Prompt 中的提示词
positive_prompt = "Spiderman in a red suit standing in middle of a crowded place, skyscrapers in the background, cinematic, neon colors, realistic look"
negative_prompt = "ugly, deformed"

# 调用函数生成图像
modified_prompt, prompt_id = prompt_image_to_image(
    prompt=base_workflow_prompt,
    positive_prompt=positive_prompt,
    negative_prompt=negative_prompt,
    input_path=DEFAULT_INPUT_PATH
    output_path=DEFAULT_OUTPUT_PATH,
    save_previews=True
)

if prompt_id:
    print(f"修改后的 Prompt: {modified_prompt}")
    print(f"生图成功 Prompt ID: {prompt_id}")
else:
    print("生图失败")